<a href="https://colab.research.google.com/github/NicholasKTaylor/Coursera_Capstone/blob/master/Week4_5.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# England And Wales Housing Affordability Versus Leisure Opportunities 
## Set up libraries

In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')



Libraries imported.


## The UK Office for National Statistices publish a set of Affordability ratios calculated by dividing house prices by gross annual residence-based earnings. Based on the median and lower quartiles of both house prices and earnings in England and Wales.  We will use this dataset.  Sheet 3c contains the ratio of median house price to median gross annual earnings organised by English County, for years 2002 to 2018.  We will use the data for 2018.  We also need geospatial coordinates for each County.

In [2]:
link='https://github.com/NicholasKTaylor/Coursera_Capstone/blob/master/ratioofhousepricetoresidencebasedearningslowerquartileandmedian.csv'
#'https://www.ons.gov.uk/file?uri=/peoplepopulationandcommunity/housing/datasets/ratioofhousepricetoresidencebasedearningslowerquartileandmedian/current/ratioofhousepricetoresidencebasedearningslowerquartileandmedian.xls'

# Read_excel and read_csv dont work with a link to a file in Colab, which is a pain.  Need to read as html and get rid of spurious first column
tables=pd.read_html(link)
df=tables[0].reset_index(drop=True)
df.head()
df.drop([df.columns[0]],axis=1,inplace=True)
# Remove redundant columns 
newIndex=['Local authority code','Local authority name','2018']
df2 = df.reindex(newIndex,axis=1)
df2.dropna(inplace=True)
df2.rename(columns={'Local authority name':'Name',
                    'Local authority code':'Code'}, 
           inplace=True)
df2.tail()




Code           Name  2018
343  W06000018     Caerphilly  4.81
344  W06000019  Blaenau Gwent  3.33
345  W06000020        Torfaen  5.20
346  W06000021  Monmouthshire  7.32
347  W06000022        Newport  5.88

In [8]:
#  Search GEO data and add to our dataframe

geolocator = Nominatim(user_agent="to_explorer")
lat=[]
lon=[]
#lat_lon.head()
for name in df2['Name'] :
  address = name + ', UK'
  location = geolocator.geocode(address)
  lat.append(location.latitude)
  lon.append(location.longitude)
  #lat_lon.append(pd.Series([name,longitude,latitude]),ignore_index=True)
 # print('The geograpical coordinate of {} are {}, {}.'.format(address,latitude, longitude))

df2['Longitude']=lon
df2['Latitude']=lat

df2.head()

Code            Name  2018  Longitude   Latitude
0  E06000047   County Durham  4.38  -1.774017  54.684832
1  E06000005      Darlington  5.29  -1.552943  54.535256
2  E06000001      Hartlepool  4.57  -1.209370  54.685728
3  E06000002   Middlesbrough  5.21  -1.235830  54.546195
4  E06000057  Northumberland  6.01  -2.000559  55.250000

In [0]:
#df2.head()
#from google.colab import drive

#drive.mount('/content/gdrive')
df2.to_csv("/content/gdrive/My Drive/Colab Notebooks/out_df2_with_lat_lon.csv",index=False)

### Get The Location of somewhere pretty central

In [24]:
address = 'Northampton, UK'

geolocator = Nominatim(user_agent="to_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Northampton are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Northampton are 52.2381355, -0.8963907.


In [25]:
# create map of England Centred On Northampton
# Zoom level of 7 is appropriate
map_Eng = folium.Map(location=[latitude, longitude], zoom_start=7)

# add markers to map
for lat, lng, label in zip(df2['Latitude'], df2['Longitude'], df2['Name']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_Eng)  
    
map_Eng

### Use Foursquare API to explore the Counties and segment them

In [9]:
# Lets just look at the first County:
county_latitude = df2.loc[327, 'Latitude'] # county latitude value
county_longitude = df2.loc[327, 'Longitude'] # county longitude value

county_name = df2.loc[327, 'Name'] # county name

print('Latitude and longitude values of {} are {}, {}.'.format(county_name, 
                                                               county_latitude, 
                                                               county_longitude))

CLIENT_ID = 'YI5XJRJ2TC1ELJE333WZYJILHOFEKJFR3T0BPKHBJ2SZL5YT' # your Foursquare ID
CLIENT_SECRET = 'PXSJSS1OTE4XZ4TLFZEL20HR50ES2DCVIDISS5AN0IK24RU2' # your Foursquare Secret
VERSION = '20191021' # Foursquare API version
LIMIT = 50 # limit of number of venues returned by Foursquare API
radius = 20000 # define radius 20km
# create URL
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    county_latitude, 
    county_longitude, 
    radius, 
    LIMIT)

results = requests.get(url).json()
results

Latitude and longitude values of Gwynedd are 52.90787985, -3.83342369061536.


{'meta': {'code': 429,
  'errorDetail': 'Quota exceeded',
  'errorType': 'quota_exceeded',
  'requestId': '5daf2a79787dba002b7dcf6a'},
 'response': {}}

### Borrow getNearbyVenues function from the labs 

In [0]:
def getNearbyVenues(names, latitudes, longitudes, radius=20000):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['County', 
                  'County Latitude', 
                  'County Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

### Find nearby venues for England

In [46]:
# Hack:  Problem with the four square interface which means it wont handle the whole dataset in one go.
# Need to split into 2 or more calls then stitch results together
first_200=df2[:200]
rest = df[200:]
#first_200.head()
#rest.head()
county_venues1 = getNearbyVenues(names=first_200['Name'],
                                   latitudes=first_200['Latitude'],
                                   longitudes=first_200['Longitude'],
                                   radius=20000
                                  )


County Durham


KeyError: ignored

In [47]:
county_venues2 = getNearbyVenues(names=rest['Name'],
                                   latitudes=rest['Latitude'],
                                   longitudes=rest['Longitude'],
                                   radius=20000
                                  )

KeyError: ignored

In [0]:
county_venues=pd.concat([county_venues1,county_venues2])

In [37]:
# Extract all the nearby venues for the England County dataset
# Use radius of 10km
#county_venues = getNearbyVenues(names=df2['Name'],
                                   latitudes=df2['Latitude'],
                                   longitudes=df2['Longitude'],
                                   radius=20000
                                  )
# Check the vebue data returned
print(county_venues.shape)
county_venues.head()

# Let's check how many venues were returned for each neighborhood
county_venues.groupby('County').count()

# Let's find out how many unique categories can be curated from all the returned venues
print('There are {} uniques categories.'.format(len(county_venues['Venue Category'].unique())))





County Durham
Darlington
Hartlepool
Middlesbrough
Northumberland
Redcar and Cleveland
Stockton-on-Tees
Gateshead
Newcastle upon Tyne
North Tyneside
South Tyneside
Sunderland
Blackburn with Darwen
Blackpool
Cheshire East
Cheshire West and Chester
Halton
Warrington
Allerdale
Barrow-in-Furness
Carlisle
Copeland
Eden
South Lakeland
Bolton
Bury
Manchester
Oldham
Rochdale
Salford
Stockport
Tameside
Trafford
Wigan
Burnley
Chorley
Fylde
Hyndburn
Lancaster
Pendle
Preston
Ribble Valley
Rossendale
South Ribble
West Lancashire
Wyre
Knowsley
Liverpool
Sefton
St. Helens
Wirral
East Riding of Yorkshire
Kingston upon Hull, City of
North East Lincolnshire
North Lincolnshire
York
Craven
Hambleton
Harrogate
Richmondshire
Ryedale
Scarborough
Selby
Barnsley
Doncaster
Rotherham
Sheffield
Bradford
Calderdale
Kirklees
Leeds
Wakefield
Derby
Leicester
Nottingham
Rutland
Amber Valley
Bolsover
Chesterfield
Derbyshire Dales
Erewash
High Peak
North East Derbyshire
South Derbyshire
Blaby
Charnwood
Harborough
Hinckle

KeyError: ignored

In [31]:
county_venues.tail()

NameError: ignored

### Analyze Each County

In [41]:
# one hot encoding
county_onehot = pd.get_dummies(county_venues[['Venue Category']], prefix="", prefix_sep="")

# add county column back to dataframe
county_onehot['County'] = county_venues['County'] 

# move neighborhood column to the first column
fixed_columns = [county_onehot.columns[-1]] + list(county_onehot.columns[:-1])
county_onehot = county_onehot[fixed_columns]

county_onehot.head()
county_onehot.shape

# Group rows by county
county_grouped = county_onehot.groupby('County').mean().reset_index()
county_grouped
county_grouped.shape

# Let's print each neighborhood along with the top 5 most common venues

num_top_venues = 5

for county in county_grouped['County']:
    print("----"+county+"----")
    temp = county_grouped[county_grouped['County'] == county].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')
    
    

----Buckinghamshire----
                venue  freq
0                 Pub  0.17
1           Gastropub  0.07
2               Hotel  0.07
3  Italian Restaurant  0.04
4                Café  0.04


----Cambridgeshire----
          venue  freq
0           Pub  0.15
1           Bar  0.07
2          Café  0.07
3   Coffee Shop  0.06
4  Burger Joint  0.05


----Cumbria----
        venue  freq
0       Hotel  0.16
1         Pub  0.16
2        Café  0.07
3  Restaurant  0.06
4         Bar  0.05


----Derbyshire----
            venue  freq
0             Pub  0.24
1            Park  0.09
2     Coffee Shop  0.06
3            Café  0.04
4  Scenic Lookout  0.04


----Devon----
       venue  freq
0        Pub  0.20
1       Café  0.08
2      Hotel  0.06
3  Gastropub  0.05
4        Bar  0.05


----Dorset----
            venue  freq
0             Pub  0.16
1           Hotel  0.08
2           Beach  0.07
3            Café  0.07
4  Scenic Lookout  0.06


----East Sussex----
       venue  freq
0        Pub  0.

In [78]:
county_grouped.head()

County  African Restaurant  Airport  Airport Lounge  \
0  Buckinghamshire                0.00      0.0             0.0   
1   Cambridgeshire                0.01      0.0             0.0   
2          Cumbria                0.00      0.0             0.0   
3       Derbyshire                0.00      0.0             0.0   
4            Devon                0.00      0.0             0.0   

   American Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0                 0.00                     0.0         0.00         0.0   
1                 0.01                     0.0         0.01         0.0   
2                 0.00                     0.0         0.00         0.0   
3                 0.00                     0.0         0.00         0.0   
4                 0.00                     0.0         0.00         0.0   

   Asian Restaurant  Athletics & Sports  BBQ Joint  Bagel Shop  Bakery   Bar  \
0              0.00                 0.0        0.0         0.0    0.01  0.00   
1              0.00                 0.0        0.0         0.0    0.03  0.07   
2              0.00                 0.0        0.0         0.0    0.02  0.05   
3              0.01                 0.0        0.0         0.0    0.02  0.02   
4              0.01                 0.0        0.0         0.0    0.02  0.05   

   Bay  Beach  Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  \
0  0.0   0.00              0.0      0.01          0.0        0.00   
1  0.0   0.00              0.0      0.00          0.0        0.00   
2  0.0   0.00              0.0      0.01          0.0        0.00   
3  0.0   0.00              0.0      0.00          0.0        0.01   
4  0.0   0.04              0.0      0.00          0.0        0.00   

   Belgian Restaurant  Bistro  Bookstore  Botanical Garden  Boutique  \
0                 0.0     0.0       0.00              0.00       0.0   
1                 0.0     0.0       0.03              0.01       0.0   
2                 0.0     0.0       0.00              0.00       0.0   
3                 0.0     0.0       0.00              0.01       0.0   
4                 0.0     0.0       0.01              0.00       0.0   

   Bowling Alley  Brazilian Restaurant  Breakfast Spot  Brewery  Bridge  \
0            0.0                   0.0            0.01     0.03     0.0   
1            0.0                   0.0            0.02     0.01     0.0   
2            0.0                   0.0            0.00     0.02     0.0   
3            0.0                   0.0            0.01     0.01     0.0   
4            0.0                   0.0            0.02     0.00     0.0   

   Buffet  Burger Joint  Burrito Place  Café  Campground  Canal  Canal Lock  \
0     0.0          0.00           0.00  0.04         0.0    0.0        0.02   
1     0.0          0.05           0.00  0.07         0.0    0.0        0.00   
2     0.0          0.00           0.00  0.08         0.0    0.0        0.00   
3     0.0          0.00           0.01  0.04         0.0    0.0        0.00   
4     0.0          0.00           0.00  0.08         0.0    0.0        0.00   

   Candy Store  Caribbean Restaurant  Castle  Cave  Cheese Shop  \
0          0.0                   0.0    0.02  0.00          0.0   
1          0.0                   0.0    0.00  0.00          0.0   
2          0.0                   0.0    0.00  0.01          0.0   
3          0.0                   0.0    0.01  0.00          0.0   
4          0.0                   0.0    0.01  0.00          0.0   

   Chinese Restaurant  Chocolate Shop  Church  Climbing Gym  Clothing Store  \
0                0.00             0.0    0.00           0.0             0.0   
1                0.01             0.0    0.01           0.0             0.0   
2                0.00             0.0    0.00           0.0             0.0   
3                0.00             0.0    0.00           0.0             0.0   
4                0.00             0.0    0.00           0.0             0.0   

   Cocktail Bar  Coffee S

### Put data into a dataframe

In [0]:
# Function to sort venues in descending order
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [43]:
#Create dataframe and display top 10 venues for each neighborhood

num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['County']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
counties_venues_sorted = pd.DataFrame(columns=columns)
counties_venues_sorted['County'] = county_grouped['County']

for ind in np.arange(county_grouped.shape[0]):
    counties_venues_sorted.iloc[ind, 1:] = return_most_common_venues(county_grouped.iloc[ind, :], num_top_venues)

counties_venues_sorted.head()

County 1st Most Common Venue 2nd Most Common Venue  \
0  Buckinghamshire                   Pub                 Hotel   
1   Cambridgeshire                   Pub                  Café   
2          Cumbria                   Pub                 Hotel   
3       Derbyshire                   Pub                  Park   
4            Devon                   Pub                  Café   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0             Gastropub                  Café    Italian Restaurant   
1                   Bar           Coffee Shop          Burger Joint   
2                  Café            Restaurant                   Bar   
3           Coffee Shop        Scenic Lookout                  Café   
4                 Hotel                   Bar             Gastropub   

          6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0                   Coffee Shop                  Park     French Restaurant   
1                     Gastropub                  Park             Bookstore   
2                   Coffee Shop                  Park           Supermarket   
3  Theme Park Ride / Attraction                 Trail         Historic Site   
4                   Coffee Shop                 Beach    Italian Restaurant   

  9th Most Common Venue 10th Most Common Venue  
0               Brewery           Dessert Shop  
1            Restaurant                 Bakery  
2        Scenic Lookout     Italian Restaurant  
3     Food & Drink Shop                Theater  
4                 Trail             Restaurant

### Cluster the neighbourhoods


In [44]:
# Run k-means to cluster the neighborhood into 5 clusters.
# set number of clusters
kclusters = 5

county_grouped_clustering = county_grouped.drop('County', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(county_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

# Let's create a new dataframe that includes the cluster as well as the top 10 venues for each county.

# add clustering labels
counties_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

county_merged = df2
county_merged.rename(columns = {'Name':'County','2018':'Affordability'}, inplace = True)


# merge county_grouped with df2 to add latitude/longitude for each neighborhood
county_merged = county_merged.join(counties_venues_sorted.set_index('County'), on='County')

county_merged.head() # check the last columns!


County  Affordability  Longitude   Latitude  Cluster Labels  \
0  Buckinghamshire          11.06  -0.750000  51.750000               4   
1   Cambridgeshire           9.02   0.083333  52.333333               2   
2          Cumbria           5.62  -2.942098  54.614314               1   
3       Derbyshire           6.04  -1.556618  53.118503               4   
4            Devon           9.42  -3.750000  50.750000               1   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0                   Pub                 Hotel             Gastropub   
1                   Pub                  Café                   Bar   
2                   Pub                 Hotel                  Café   
3                   Pub                  Park           Coffee Shop   
4                   Pub                  Café                 Hotel   

  4th Most Common Venue 5th Most Common Venue         6th Most Common Venue  \
0                  Café    Italian Restaurant                   Coffee Shop   
1           Coffee Shop          Burger Joint                     Gastropub   
2            Restaurant                   Bar                   Coffee Shop   
3        Scenic Lookout                  Café  Theme Park Ride / Attraction   
4                   Bar             Gastropub                   Coffee Shop   

  7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0                  Park     French Restaurant               Brewery   
1                  Park             Bookstore            Restaurant   
2                  Park           Supermarket        Scenic Lookout   
3                 Trail         Historic Site     Food & Drink Shop   
4                 Beach    Italian Restaurant                 Trail   

  10th Most Common Venue  
0           Dessert Shop  
1                 Bakery  
2     Italian Restaurant  
3                Theater  
4             Restaurant

In [22]:
# !wget --quiet https://github.com/NicholasKTaylor/Coursera_Capstone/blob/master/NUTS_Level_3_UK.geojson -O counties.json

#url='https://github.com/NicholasKTaylor/Coursera_Capstone/blob/master'
#counties = f'{url}/NUTS_Level_3_UK.geojson'
#print('GeoJSON file downloaded!')    
#geojson = r'counties.json' # geojson file

from google.colab import drive

drive.mount('/content/gdrive')
!ls -l /content/gdrive/My\ Drive/Colab\ Notebooks
#print json['unit']

#with open("counties") as json_file:
#with open('counties.json') as jsonfile:
#  for line in jsonfile:
#    print(line)
    #data = json.load(jsonfile)
#data
#json_data = json.load(counties)
#print(json_data)

#url = 'https://raw.githubusercontent.com/python-visualization/folium/master/examples/data'
#state_geo = f'{url}/us-states.json'

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3Aietf%3Awg%3Aoauth%3A2.0%3Aoob&scope=email%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdocs.test%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive.photos.readonly%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fpeopleapi.readonly&response_type=code

Enter your authorization code:
··········
Mounted at /content/gdrive
counties.json  gdrive  sample_data


In [33]:
# !ls -l */*/*
data='/content/gdrive/My Drive/Colab Notebooks/NUTS_Level_3_UK.geojson'
with open(data) as jsonfile:
  for line in jsonfile:
    print(line)

{"type":"FeatureCollection","features":[{"type":"Feature","properties":{"objectid":1,"nuts318cd":"UKC11","nuts318nm":"Hartlepool and Stockton-on-Tees","bng_e":444952,"bng_n":522016,"long":-1.30587006,"lat":54.59135056,"st_areashape":298478046.1895426,"st_lengthshape":134296.06209107605},"geometry":{"type":"MultiPolygon","coordinates":[[[[-1.2585613974951761,54.72605545021356],[-1.2702517668900413,54.727168685983855],[-1.2903014571935307,54.718397844388996],[-1.305520892127565,54.717521651384516],[-1.3013266803430166,54.708101048196575],[-1.3138494867620187,54.70122750804094],[-1.3126374286427225,54.69599671187722],[-1.3193293729333861,54.69135684605863],[-1.3445259837768542,54.6911209109247],[-1.3344403320390839,54.68904660945338],[-1.3309457683685693,54.68213366004915],[-1.3330384068579506,54.672652582366226],[-1.3435301366934718,54.66862089640206],[-1.347851513531327,54.662420925425565],[-1.3412542291937026,54.65021189685747],[-1.383763954552296,54.64624300048311],[-1.380898316350907

In [60]:
county_json = json.load(open('/content/gdrive/My Drive/Colab Notebooks/NUTS_Level_3_UK.geojson')) 
for x in county_json['features'] : 
    print (x['properties'])

{'objectid': 1, 'nuts318cd': 'UKC11', 'nuts318nm': 'Hartlepool and Stockton-on-Tees', 'bng_e': 444952, 'bng_n': 522016, 'long': -1.30587006, 'lat': 54.59135056, 'st_areashape': 298478046.1895426, 'st_lengthshape': 134296.06209107605}
{'objectid': 2, 'nuts318cd': 'UKC12', 'nuts318nm': 'South Teesside', 'bng_e': 461718, 'bng_n': 519597, 'long': -1.04694998, 'lat': 54.56784821, 'st_areashape': 299101636.4990195, 'st_lengthshape': 97434.22888509424}
{'objectid': 3, 'nuts318cd': 'UKC13', 'nuts318nm': 'Darlington', 'bng_e': 428029, 'bng_n': 515649, 'long': -1.56834996, 'lat': 54.5353508, 'st_areashape': 197366312.97138715, 'st_lengthshape': 98163.3685905879}
{'objectid': 4, 'nuts318cd': 'UKC14', 'nuts318nm': 'Durham CC', 'bng_e': 410381, 'bng_n': 532242, 'long': -1.8405, 'lat': 54.68513107, 'st_areashape': 2232196917.132352, 'st_lengthshape': 281536.9464399625}
{'objectid': 5, 'nuts318cd': 'UKC21', 'nuts318nm': 'Northumberland', 'bng_e': 395323, 'bng_n': 600699, 'long': -2.07521009, 'lat': 5

### Now we can visualise the clusters


In [52]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=7,tiles='Mapbox Bright')

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(county_merged['Latitude'], county_merged['Longitude'], county_merged['County'], county_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
    
#!wget --quiet https://data.gov.uk/dataset/cd97a8df-e2fe-4f3d-a60f-1f871a317d31/counties-and-unitary-authorities-december-2016-full-extent-boundaries-in-england-and-wales -O counties.json    
#countries/united-kingdom/uk-counties.json
#  print('GeoJSON file downloaded!')    
geojson = r'/content/gdrive/My Drive/Colab Notebooks/NUTS_Level_3_UK.geojson' # geojson file
map_clusters.choropleth(
    geo_data=geojson,
    name='House Price Affordability',
    data=county_merged,
    columns=['County', 'Affordability'],
    fill_color='YlGn',
    fill_opacity=0.7, 
    line_opacity=0.2,
    key_on='nuts218nm',
    legend_name='Affordability'
)     
map_clusters



/usr/local/lib/python3.6/dist-packages/folium/folium.py:426: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  FutureWarning
